In [2]:
from validator.InstanceCO22 import InstanceCO22
import warnings
from collections import OrderedDict
warnings.filterwarnings( "ignore", module = "matplotlib\..*" )
from util import *
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import networkx as nx
from vrpy import VehicleRoutingProblem
import pprint
import warnings
import logging
import llist
import pandas as pd
from typing import List, Set, Tuple, Dict
import random
import time
import copy

warnings.filterwarnings("ignore", module="vrpy\..*")


logger = logging.getLogger(__name__)
logging.basicConfig(level=logging.CRITICAL)
%load_ext autoreload
%autoreload 1

## Initial solution

In [3]:
def distance(loc1: InstanceCO22.Location, loc2: InstanceCO22.Location, ceil: bool = True) -> float:
    dist = math.sqrt((loc1.X - loc2.X)**2 + (loc1.Y - loc2.Y)**2)
    if ceil:
        return math.ceil(dist)
    else:
        return dist


def requestClosestHub(instance: InstanceCO22, request: InstanceCO22.Request) -> int:
    nHubs = len(instance.Hubs)
    hubs = instance.Locations[1:nHubs+1]
    minDist = math.inf
    minDistHubLocID = None
    for i, hub in enumerate(hubs):
        if request.ID in instance.Hubs[i].allowedRequests:
            hubDist = distance(
                instance.Locations[request.customerLocID-1], hub)
            if hubDist < minDist:
                minDist = hubDist
                minDistHubLocID = hub.ID
    return minDistHubLocID


def requestsClosestHub(instance: InstanceCO22) -> dict:
    # return dictionary of {'LOC_ID': ' NEAREST LOC_ID'}
    res = {}
    for req in instance.Requests:
        res[req.ID] = requestClosestHub(instance, req)
    return res


def requestsPerHub(instance: InstanceCO22) -> dict:
    closestHubPerRequest = requestsClosestHub(instance=instance)
    nHubs = len(instance.Hubs)
    hubLocIDs = list(range(2, nHubs+2))
    res = {val: [] for val in hubLocIDs}
    for hubLocID in hubLocIDs:
        for reqID, closestHubLocID in closestHubPerRequest.items():
            if closestHubLocID is hubLocID:
                res[hubLocID].append(reqID)
    return res


def amountPerProduct(instance: InstanceCO22, requests: list) -> list:
    nProducts = len(instance.Products)
    res = [None]*nProducts
    for i in range(nProducts):
        res[i] = sum([req.amounts[i] for req in requests])
    return res


def filterRequests(instance: InstanceCO22, day: int = None, locationsID: int = None) -> list:
    res = instance.Requests.copy()
    if day != None:
        res = [_ for _ in res if _.desiredDay is day]
    if locationsID != None:
        res = [_ for _ in res if _.customerLocID in locationsID]
    return res


def addAllEdges(G: nx.DiGraph, checkWindowOverlap: bool = False) -> nx.DiGraph:
    for locID1, node1 in G.nodes(data=True):
        for locID2, node2 in G.nodes(data=True):
            if locID1 != locID2:
                if checkWindowOverlap and locID1 not in ["Source", "Sink"] and locID2 not in ["Source", "Sink"] and not windowOverlap(node1['periodIDs'], node2['periodIDs']):
                    continue
                dist = math.ceil(
                    math.sqrt(pow(node1['X']-node2['X'], 2) + pow(node1['Y']-node2['Y'], 2)))
                if locID1 == "Sink" or locID2 == "Source" or (locID1 == "Source" and locID2 == "Sink"):
                    continue
                else:
                    G.add_edge(locID1, locID2, time=dist, cost=dist)
    return G


def createNxHub(instance: InstanceCO22, hubLocID: int, requests: list) -> nx.DiGraph:
    G = nx.DiGraph()
    for req in requests:
        reqLoc = instance.Locations[req.customerLocID-1]
        G.add_node(req.ID, locID=reqLoc.ID, reqID=req.ID, X=reqLoc.X,
                   Y=reqLoc.Y, demand=sum(req.amounts), amounts=req.amounts)
    hubLoc = instance.Locations[hubLocID]
    G.add_node("Source", locID=hubLocID, X=hubLoc.X, Y=hubLoc.Y)
    G.add_node("Sink", locID=hubLocID, X=hubLoc.X, Y=hubLoc.Y)
    G = addAllEdges(G)
    return G


def solveHubVRP(instance: InstanceCO22, hubLocID: int, requests: list) -> dict:
    # create networkX
    G = createNxHub(instance, hubLocID, requests)
    G_dict = {i: v for i, v in G.nodes(data=True)}
    # print(G_dict.keys())
    prob = VehicleRoutingProblem(G, load_capacity=instance.VanCapacity)
    prob.duration = instance.VanMaxDistance
    prob.fixed_cost = instance.VanDayCost
    prob.solve()
    best_routes = prob.best_routes
    #best_routes = {id:listReplace(best_routes[id], ["Source","Sink"], hubLocID) for id in best_routes.keys()}
    res = {
        'routes': {key: {'route': [G_dict[id] for id in best_routes[key]]} for key in best_routes.keys()},
        'demand': sum([sum(req.amounts) for req in requests]),
        'amounts': amountPerProduct(instance, requests)
    }
    return res


def createNxDepot(instance: InstanceCO22, dayRoutes: dict) -> nx.DiGraph:
    G = nx.DiGraph()
    # add hubs
    for (day, hubLocID), hubData in dayRoutes.items():
        G.add_node(f"{hubLocID}.1", locID=hubLocID, demand=0, amounts=0,
                   X=instance.Locations[hubLocID-1].X, Y=instance.Locations[hubLocID-1].Y)

    for (day, hubLocID), hubData in dayRoutes.items():
        i = 1
        nodeID = f"{hubLocID}.{i}"
        while nodeID in G.nodes and G.nodes[nodeID]['demand'] + hubData['demand'] > instance.TruckCapacity:
            i += 1
            nodeID = f"{hubLocID}.{i}"
        if nodeID not in G.nodes:
            G.add_node(nodeID, locID=hubLocID, demand=0, amounts=0,
                       X=instance.Locations[hubLocID-1].X, Y=instance.Locations[hubLocID-1].Y)

        G.nodes[nodeID]['amounts'] = list(
            np.array(G.nodes[nodeID]['amounts']) + np.array(hubData['amounts']))
        G.nodes[nodeID]['demand'] = G.nodes[nodeID]['demand']+hubData['demand']

    G.add_node("Source", locID=1,
               X=instance.Locations[0].X, Y=instance.Locations[0].Y)
    G.add_node("Sink", locID=1,
               X=instance.Locations[0].X, Y=instance.Locations[0].Y)

    G = addAllEdges(G)
    return G


def solveDepotVRP(instance: InstanceCO22, dayRoutes: dict) -> dict:
    # for solving per day
    G = createNxDepot(instance, dayRoutes)
    G_dict = {i: v for i, v in G.nodes(data=True)}
    print(G_dict.keys())

    prob = VehicleRoutingProblem(G, load_capacity=instance.TruckCapacity)
    prob.duration = instance.TruckMaxDistance
    prob.fixed_cost = instance.TruckDayCost
    prob.solve()
    best_routes = prob.best_routes
    print(best_routes)
    #best_routes = {id:listReplace(best_routes[id], ["Source","Sink"], hubLocID) for id in best_routes.keys()}
    res = {key: [G_dict[id] for id in best_routes[key]]
           for key in best_routes.keys()}
    print(res)
    return res

def solveHub(instance: InstanceCO22) -> dict:
    nDays = instance.Days
    nHubs = len(instance.Hubs)
    hubLocIDs = list(range(2,nHubs+2))
    hubClusters = requestsPerHub(instance)
    hubRoutes = {}  
    for day in range(1, nDays+1):                                                   #hub routing
        dayRoutes = {}
        for hubLocID in hubLocIDs:
            hubCluster = hubClusters[hubLocID]
            #requestsToServe = filterRequests(instance, day, hubCluster)
            requestsToServe =[_ for _ in instance.Requests if _.ID in hubCluster and _.desiredDay is day]
            print(hubCluster, [_.ID for _ in requestsToServe])   #
            if(len(requestsToServe) > 0):
                dayHubRoutes = solveHubVRP(instance, hubLocID, requestsToServe)
                dayRoutes[hubLocID] = dayHubRoutes
        hubRoutes[day] = dayRoutes
    return hubRoutes

In [415]:
%%capture
instance = loadInstance(10)
res = solveHub(instance)

INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 1084 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1084 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1084.0
INFO:vrpy.master_solve_pulp:total cost = 1084.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 1032 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1032 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1032.0
INFO:vrpy.master_solve_pulp:total cost = 1032.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 1068 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 1068 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 1068.0
INFO:vrpy.master_solve_pulp:total cost = 1068.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 1085 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 10

In [4]:
class DistanceMatrix(object):
    #allows to get distance between to Location IDs or two Request IDs
    
    def __init__(self, instance: InstanceCO22):
        self.locIDs = [_.ID for _ in instance.Locations]
        distances = self._computeDistanceMatrix(instance)
        self.dmDf = pd.DataFrame(index = self.locIDs, columns=self.locIDs, data = distances)

    def _computeDistanceMatrix(self, instance: InstanceCO22, roundUp: bool = True) -> np.ndarray:
        # https://stackoverflow.com/questions/22720864/efficiently-calculating-a-euclidean-distance-matrix-using-numpy
        
        z = np.array([complex(l.X, l.Y) for l in instance.Locations])
        m, n = np.meshgrid(z, z)
        out = abs(m-n)
        if roundUp:
            out = np.ceil(out)
        return out

    def byReqID(self, reqID1, reqID2):
        locID1 = self._getLocID(reqID1)
        locID2 = self._getLocID(reqID2)
        return self.byLocID(locID1, locID2)

    def byLocID(self, locID1, locID2):
        return self.dmDf.loc[locID1, locID2]

    def byReqIDLocID(self, reqID1, locID2):
        locID1 = self._getLocID(reqID1)
        return self.byLocID(locID1, locID2)

    def _getLocID(self, reqID):
        return instance.Requests[reqID-1].customerLocID

In [418]:
dm = DistanceMatrix(instance)
sum([dm.byReqID(i,i+1) for i in range(1,len(instance.Requests))])

4667.0

In [5]:
class Node(object):
    def __init__(self, reqID=None, locID=None, amounts=None, X=None, Y=None, isHub=False):
        # suggest id: requestDI
        self.reqID = reqID
        self.locID = locID
        self.amounts = amounts
        if amounts is not None:
            self.demand = sum(amounts)
        self.isHub = isHub
        self.X = X
        self.Y = Y

    def fromRequest(self, req: InstanceCO22.Request):
        self.reqID = req.ID
        self.locID = req.customerLocID
        self.amounts = req.amounts
        if type(req.amounts) is List:
            self.demand = sum(req.amounts)
        else:
            self.demand = req.amounts
        self.isHub = False
        self.X = None
        self.Y = None
        return self

    def __repr__(self):
        return f"Node(reqID:{self.reqID}, locID:{self.locID})"


class HubRoute(object):

    def __init__(self, routeID, hubLocID):
        self.nodes = []
        self.routeID = routeID
        self.hubLocID = hubLocID
        self.cachedDistance = None

    def addNode(self, node: Node):
        # add node to end of route
        self.nodes.append(node)
        self.cachedDistance = None
        return self

    def addNodes(self, nodes: List[Node]):
        for node in nodes:
            self.addNode(node)
        return self

    def insertNodeAfter(self, i, newNode: Node):
        # insert node after specified index
        #appendAfterIndex = self._findIndexOfID(reqID)
        self.nodes.insert(i+1, newNode)
        self.cachedDistance = None
        return self

    def insertNodeBefore(self, i, newNode: Node):
        # insert node after specified index
        #appendBeforeIndex = self._findIndexOfID(reqID)
        self.nodes.insert(i, newNode)
        self.cachedDistance = None
        return self

    def deleteNode(self, node):
        self.nodes.remove(node)

    def deleteNodeByReqID(self, reqID):
        indexToDelete = self._findIndexOfID(reqID)
        self.nodes = [j for i, j in enumerate(self.nodes) if i != indexToDelete ]

    def replaceNode(self, reqID, newNode: Node):
        indexToReplace = self._findIndexOfID(reqID)
        self.nodes[indexToReplace] = newNode
        self.cachedDistance = None
        return self

    def swapNodes(self, ind1, ind2):
        self.nodes[ind1], self.nodes[ind2] = self.nodes[ind2], self.nodes[ind1]
        self.cachedDistance = None
        return self

    def _findIndexOfID(self, nodeID):
        i = 0
        el = self.nodes[i]

        while el.reqID != nodeID:
            i += 1
            el = self.nodes[i]

        return i

    def length(self, distanceMatrix: DistanceMatrix): #distance length
        if self.cachedDistance:
            return self.cachedDistance
        
        #distance between nodes (clients)
        dist = 0
        for i in range(0, len(self.nodes)-1):
            dist += distanceMatrix.byLocID(self.nodes[i].locID, self.nodes[i+1].locID)

        #distance from hub to first node and from last node to hub
        dist += distanceMatrix.byLocID(self.hubLocID, self.nodes[0].locID)
        dist += distanceMatrix.byLocID(self.hubLocID, self.nodes[-1].locID)
        self.cachedDistance = dist
        return dist

    def demand(self):
        return sum(_.demand for _ in self.nodes)

    def amounts(self):
        nProducts = len(self.nodes[0].amounts)
        res = []
        for i in range(nProducts):
            res.append(sum([_.amounts[i] for _ in self.nodes]))
        return res

    def nProducts(self):
        return len(self.nodes[0].amounts)


    def __repr__(self):
        return f"HubRoute from hub {self.hubLocID}: " + " -> ".join([_.__repr__() for  _ in self.nodes])

    def __len__(self): #nodes (except hub)
        return len(self.nodes)
    
    def __getitem__(self, i):
        return self.nodes[i]

In [6]:
#test route distance and demand calculation 

#add all requests in one route orderer by reqID
hubLocID = 2
nodes = [Node(_.ID, _.customerLocID, _.amounts, instance.Locations[_.customerLocID-1].X, instance.Locations[_.customerLocID-1].Y, isHub=False) for _ in instance.Requests]
route = HubRoute(routeID=1, hubLocID=hubLocID)
route.addNodes(nodes)
dm = DistanceMatrix(instance)

assert route.length(distanceMatrix = dm) == sum([dm.byReqID(i,i+1) for i in range(1,len(instance.Requests))]) + dm.byReqIDLocID(instance.Requests[0].ID,hubLocID) + dm.byReqIDLocID(instance.Requests[-1].ID,hubLocID)
assert route.demand() == sum([sum(_.amounts) for _ in instance.Requests])
assert route.demand() == sum(route.amounts())
#test route insertion  after id. 
node1= Node(1,1,[1,1,1],10,1)
node2= Node(2,1,[1,1,1],10,1)
node3= Node(3,1,[1,1,1],10,1)
node4= Node(4,1,[1,1,1],10,1)
route = HubRoute(1,1)
route.addNodes([node1, node2, node3]) 
route.insertNodeAfter(2, node4) # insert node4 after reqID 2
route
assert route.nodes[2].reqID == 4

node4= Node(5,1,[1,1,1],10,1)
route.replaceNode(1,node4)
assert route.nodes[0].reqID == 5


NameError: name 'instance' is not defined

In [722]:
a = [1,2,3,4,5]
a.insert(6,6)
a

[1, 2, 3, 4, 5, 6]

In [720]:
random.randint(0,5+1)

3

In [7]:

class DayHubRoutes(object):
    def __init__(self):
        self.routes = []

    def addRoute(self, route: HubRoute):
        self.routes.append(route)

    def addRouteFromNodes(self, routeID, hubLocID, nodes: List[Node]):
        route = HubRoute(routeID, hubLocID).addNodes(nodes)
        self.routes.append(route)
        self.hubsUsed.add(hubLocID)
        # nodes: [nodeID1, nodeID2, nodeID3, nodeID4]

    def computeCost(self, vanDistanceCost, vanDayCost, distanceMatrix: DistanceMatrix):
        # compute cost of distance and #vans
        cost = 0
        for route in self.routes:
            cost += route.length(distanceMatrix) * vanDistanceCost
            cost += vanDayCost
        return cost

    def coversRequestIDs(self, requestIDs: List[int], verbose=False) -> bool:
        reqsToServe = requestIDs.copy()
        for route in self.routes:
            for node in route.nodes:
                reqsToServe.remove(node.reqID) if node.reqID in reqsToServe else None
        allServed = (len(reqsToServe) == 0)
        if not allServed and verbose:
            print(allServed, "not served")
        return allServed

    def getRoutesFromHub(self, hubLocID) -> List[HubRoute]:
        res = []
        for route in self.routes:
            if route.hubLocID is hubLocID:
                res.append(route)
        return res

    def nHubs(self):
        return len(self.hubsUsed())
    
    def hubsUsed(self):
        res = set()
        for route in self.routes:
            res.add(route.hubLocID)
        return res

    def isFeasible(self, vanCapacity, vanMaxDistance, distanceMatrix, verbose=False) -> bool:
        # check max capacity and maxdistance constraints. None of the operators will remove nodes from the routes so it is assumed that
        # if all requests are served in the initial solution this will be the case for all derived solutions.
        notOverCapacity = True
        notOverDistance = True
        for route in self.routes:
            if route.demand() > vanCapacity:
                if verbose:
                    print(
                        f"Route with id {route.routeID} has a demand of {route.demand()} > vanCapacity = {vanCapacity}")
                notOverCapacity = False
            routeLength = route.length(distanceMatrix)
            if routeLength > vanMaxDistance:
                if verbose:
                    print(
                        f"Route with id {route.routeID} has a length of {routeLength} > vanMaxDistance = {vanMaxDistance}")
                notOverDistance = False
        feasible = notOverCapacity and notOverDistance
        return feasible

    def __repr__(self):
        res = ""
        for route in self.routes:
            res+= route.__repr__() + "\n"
        return res
    
    def __len__(self):
        return len(self.routes)

    # operators for neighbourhood exploration
    #   Based on Kuo, Wang

    def randomNodeInsertion(self):
        # Delete node from a route and insert inbetween two succesive nodes (in any route)

        r1 = random.choice(self.routes)     #choose random route r1
        n1 = random.choice(r1)              #choose random node n1 from route r1
        r2 = random.choice(self.routes)     #choose next random route r2
        #print(n2.reqID)   
        #print(r2.nodes[0].reqID)
        r1.deleteNode(n1)  
        insertBefore = random.randint(0,len(r2)+1)            #choose next random node n2             
        r2.insertNodeBefore(insertBefore, n1)    #insert n1 in route r2 after node n2
        if len(r1) == 0:
            self.routes.remove(r1)
        return self

    def shuffleRoute(self):
        #shuffle two nodes within one route
        r1 = random.choice(self.routes)     #choose random route r1
        if(len(r1) == 1):
            return self
        node1 = random.randint(0,len(r1)-1)            #choose next random node n2  
        node2 = random.randint(0,len(r1)-1)   
        while node2 == node1:
            node2 = random.randint(0,len(r1)-1)  
        #print(r1)
        r1.swapNodes(node1, node2)    
        #print(r1)
        return self


    def randomNodeExchange():
        # Select two nodes and switch position (can be in different routes)
        raise NotImplementedError

    def randomArcExchange():
        # Select two pairs of nodes and exchange positions
        raise NotImplementedError

    def randomMoveRouteToHub():
        raise NotImplementedError
    
    def randomMoveRoutesToNearestHub():
        raise NotImplementedError

    def randomSectionExchange():
        # Select two sections from two different routes and exchange sections
        raise NotImplementedError

class HubRoutes(object):
    def __init__(self):
        self.hubRoutes = {}
        
    def addDayHubRoutes(self,day, dayHubRoutes: DayHubRoutes):
        self.hubRoutes[day] = dayHubRoutes

    def computeCost(self, vanDistanceCost, vanDayCost, vanCost, distanceMatrix: DistanceMatrix):
        cost = 0
        for day, dayHubRoutes in self.hubRoutes.items():
            cost += dayHubRoutes.computeCost(vanDistanceCost, vanDayCost, distanceMatrix)
        cost += self.nVansRequired() * vanCost
        return cost

    def nVansRequired(self):
        return max([len(dayHubRoutes) for day, dayHubRoutes in self.hubRoutes.items()])
    
    def toDict(self, instance):
        res = {}
        for day, dayHubRoutes in self.hubRoutes.items():
            dayres = {}
            for locID in dayHubRoutes.hubsUsed():
                dayres[locID] = {}
                hub = instance.Locations[locID]
                hubNode = {'X': hub.X,'Y':hub.Y,'locID': locID}
                hubRoutes = dayHubRoutes.getRoutesFromHub(locID)
                nProducts = hubRoutes[0].nProducts()
                dayres[locID]['routes'] = {}
                i = 0
                for route in hubRoutes:
                    dayres[locID]['routes'][i] = {}
                    dayres[locID]['routes'][i]['route'] = [hubNode] + [{'X': n.X,'Y':n.Y,'demand':n.demand,'locID':n.locID,'reqID':n.reqID} for n in route.nodes] + [hubNode]
                    i+=1
                dayres[locID]['amounts'] = [sum([route.amounts()[i] for route in hubRoutes]) for i in range(nProducts)]
                dayres[locID]['demand'] = sum([route.demand() for route in hubRoutes])
            res[day] = dayres
        return res
        
    def __repr__(self):
        res = ""
        for day, data in self.hubRoutes.items():
            res += "-"*10 + f"day {day}" + "-"*10 + "\n"
            res += data.__repr__() + "\n"
        return res

    def __getitem__(self,i):
        return self.hubRoutes[i]


In [8]:
def parseToDayHubroutes(res):
    i = 0
    hubRoutesObject = HubRoutes()
    #take dictionary with structure as hubRoutes datamodel
    for day, dayData in res.items():
        dayHubRoutesObject = DayHubRoutes()
        for hubLocID, hubData in dayData.items():
            for routeID, routeData in hubData['routes'].items():
                route = HubRoute(i, hubLocID)
                for node in routeData['route'][1:-1]: #ignore source and sink
                    nodeObject = Node(reqID = node['reqID'], locID=node['locID'], amounts=node['amounts'], X=node['X'], Y=node['Y'])
                    route.addNode(nodeObject)
                dayHubRoutesObject.addRoute(route)
        hubRoutesObject.addDayHubRoutes(day=day,dayHubRoutes=dayHubRoutesObject)
    return hubRoutesObject

In [763]:
#test DayHubRoutes distance and demand calculation 

#add all requests in one route orderer by reqID
nodes = [Node(_.ID, _.customerLocID, _.amounts, instance.Locations[_.customerLocID-1].X, instance.Locations[_.customerLocID-1].Y, isHub=False) for _ in instance.Requests]

route1 = HubRoute(routeID=1, hubLocID=1)
route1.addNodes(nodes[0:10])

route2 = HubRoute(routeID=2, hubLocID=2)
route2.addNodes(nodes[10:20])

dayHubRoutes = DayHubRoutes()
dayHubRoutes.addRoute(route1)
dayHubRoutes.addRoute(route2)
dayHubRoutes.addRoute(route2)
print(dayHubRoutes.hubsUsed)
print(dayHubRoutes.nHubs())
print(dayHubRoutes.isFeasible(instance.VanCapacity, instance.VanMaxDistance, dm, verbose=True))
print(dayHubRoutes.coversRequestIDs([1,2,3,4,5]))



<bound method DayHubRoutes.hubsUsed of HubRoute from hub 1: Node(reqID:1, locID:4) -> Node(reqID:2, locID:22) -> Node(reqID:3, locID:12) -> Node(reqID:4, locID:23) -> Node(reqID:5, locID:22) -> Node(reqID:6, locID:16) -> Node(reqID:7, locID:7) -> Node(reqID:8, locID:6) -> Node(reqID:9, locID:11) -> Node(reqID:10, locID:6)
HubRoute from hub 2: Node(reqID:11, locID:8) -> Node(reqID:12, locID:12) -> Node(reqID:13, locID:12) -> Node(reqID:14, locID:5) -> Node(reqID:15, locID:12) -> Node(reqID:16, locID:11) -> Node(reqID:17, locID:9) -> Node(reqID:18, locID:5) -> Node(reqID:19, locID:12) -> Node(reqID:20, locID:20)
HubRoute from hub 2: Node(reqID:11, locID:8) -> Node(reqID:12, locID:12) -> Node(reqID:13, locID:12) -> Node(reqID:14, locID:5) -> Node(reqID:15, locID:12) -> Node(reqID:16, locID:11) -> Node(reqID:17, locID:9) -> Node(reqID:18, locID:5) -> Node(reqID:19, locID:12) -> Node(reqID:20, locID:20)
>
2
Route with id 1 has a demand of 52 > vanCapacity = 30
Route with id 2 has a demand o

## Local Search 

In [9]:


def checkBetterState(neighBour, costs, state, stateCost, dm, msg=None):
    if neighBour.isFeasible(instance.VanCapacity, instance.VanMaxDistance, dm):
            neighBourCost = neighBour.computeCost(instance.VanDistanceCost, instance.VanDayCost, dm)
            costs.append(neighBourCost)
            if neighBourCost < stateCost:
                stateCost = neighBourCost
                print("New best: ", stateCost, i)
                print(state)
                print(neighBour)
                print(msg) if msg else None
                state = neighBour
    return neighBour, costs, state, stateCost



def localSearchDayHubRoutes(instance, dayHubRoutes: DayHubRoutes, maxTimeSeconds, maxIterations, nStart=5):
    maxTimeSeconds = maxTimeSeconds/nStart
    maxIterations = maxIterations/nStart
    dm = DistanceMatrix(instance)
    bestState = None
    bestStateCost = math.inf
    for iteration in range(nStart):

        startTime = time.time()
        costs = [dayHubRoutes.computeCost(
            instance.VanDistanceCost, instance.VanDayCost, dm)]
        state = dayHubRoutes
        stateCost = costs[0]
        i = 0

        print("Starting at ", stateCost)
        while time.time() - startTime < maxTimeSeconds and i < maxIterations:
            
            neighBour = copy.deepcopy(state)
            neighBour.randomNodeInsertion()
            neighBour, costs, state, stateCost =checkBetterState(neighBour, costs, state, stateCost, dm, msg="randomNodeInsertion")


            neighBour = copy.deepcopy(state)
            #print("routeshuffle")
            neighBour.shuffleRoute()
            neighBour, costs, state, stateCost =checkBetterState(neighBour, costs, state, stateCost, dm,  msg="routeshuffle")

            i += 1

        print(i)

        if stateCost < bestStateCost:
            bestState = state
            bestStateCost = stateCost

    return bestState, bestStateCost


def localSearchHubRoutes(instance, hubRoutes: HubRoutes, maxTimeSeconds, maxIterations=math.inf, nStart=5):
    res = HubRoutes()
    for day, dayHubRoutes in hubRoutes.hubRoutes.items():
        print("="*10, day, "="*10)
        if len(dayHubRoutes) > 0:
            dayres = localSearchDayHubRoutes(
                instance, dayHubRoutes, maxTimeSeconds, maxIterations, nStart)
        else:
            dayres = [DayHubRoutes()]
        res.addDayHubRoutes(day, dayres[0])
    return res


In [804]:
instance = loadInstance(6)
res = solveHub(instance)
test = parseToDayHubroutes(res)

INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 168 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 168 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 168.0
INFO:vrpy.master_solve_pulp:total cost = 168.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 256.0


[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] [2]
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] [3]


INFO:vrpy.master_solve_pulp:total cost = 256.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 178 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 178 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 178.0
INFO:vrpy.master_solve_pulp:total cost = 178.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 220 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 220 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 220.0


[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] [1]
[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] []
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] []
[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] [4, 5]


INFO:vrpy.vrp:iteration 1, 220.0
INFO:vrpy.vrp:iteration 2, 220.0
INFO:vrpy.master_solve_pulp:total cost = 220.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 164 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 164 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 164.0
INFO:vrpy.master_solve_pulp:total cost = 164.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 194.0
INFO:vrpy.master_solve_pulp:total cost = 194.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 178 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 178 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 178.0


...

[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] [40]
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] []
[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] [39, 41]
[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] []
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] [42, 43, 44]


INFO:vrpy.vrp:iteration 1, 365.0
INFO:vrpy.master_solve_pulp:total cost = 470.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 168 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 168 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 168.0
INFO:vrpy.master_solve_pulp:total cost = 168.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 256.0
INFO:vrpy.master_solve_pulp:total cost = 256.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 150.0
INFO:vrpy.master_solve_pulp:total cost = 150.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 1

[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] []
[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] [45]
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] [46]
[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] []
[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] [47]
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] []
[] []
[7, 8, 13, 16, 31, 32, 49] []
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] [48]


INFO:vrpy.vrp:iteration 0, 192.0
INFO:vrpy.master_solve_pulp:total cost = 192.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 194 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 194.0
INFO:vrpy.master_solve_pulp:total cost = 194.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 164 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 164 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 164.0
INFO:vrpy.master_solve_pulp:total cost = 164.0


[2, 14, 15, 28, 34, 36, 40, 45, 47, 50] [50]
[3, 12, 17, 18, 19, 22, 23, 33, 42, 43, 44, 46] []
[] []
[7, 8, 13, 16, 31, 32, 49] [49]
[1, 4, 5, 6, 9, 10, 11, 20, 21, 24, 25, 26, 27, 29, 30, 35, 37, 38, 39, 41, 48] []


In [805]:
#print(pprint.pformat(res))
print(test.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost, dm))
ls_result = localSearchHubRoutes(instance, test, maxTimeSeconds=5)
print(ls_result.computeCost(instance.VanDistanceCost, instance.VanDayCost,instance.VanCost, dm))

350270.0
========== 1 ==========
Starting at  3340.0
routeshuffle
routeshuffle
New best:  2460.0 8
HubRoute from hub 2: Node(reqID:2, locID:7)
HubRoute from hub 3: Node(reqID:3, locID:21)
HubRoute from hub 6: Node(reqID:1, locID:19)

HubRoute from hub 3: Node(reqID:2, locID:7) -> Node(reqID:3, locID:21)
HubRoute from hub 6: Node(reqID:1, locID:19)

randomNodeInsertion
routeshuffle
HubRoute from hub 3: Node(reqID:2, locID:7) -> Node(reqID:3, locID:21)
HubRoute from hub 3: Node(reqID:3, locID:21) -> Node(reqID:2, locID:7)
New best:  760.0 8
HubRoute from hub 3: Node(reqID:2, locID:7) -> Node(reqID:3, locID:21)
HubRoute from hub 6: Node(reqID:1, locID:19)

HubRoute from hub 3: Node(reqID:1, locID:19) -> Node(reqID:2, locID:7) -> Node(reqID:3, locID:21)

randomNodeInsertion
routeshuffle
HubRoute from hub 3: Node(reqID:1, locID:19) -> Node(reqID:2, locID:7) -> Node(reqID:3, locID:21)
HubRoute from hub 3: Node(reqID:1, locID:19) -> Node(reqID:3, locID:21) -> Node(reqID:2, locID:7)
routeshuff

KeyboardInterrupt: 

## Finishing using greedy02

In [10]:
def extractDays(hubRoutes, days: list) -> dict:
    res = {}
    for day, dayRoutes in hubRoutes.items():
        if day in days:
            for hubLocID in dayRoutes:
                newID = (day, hubLocID)
                res[newID] = dayRoutes[hubLocID]
    return res
    
def solve(instance: InstanceCO22) -> dict:
    nDays = instance.Days
    nHubs = len(instance.Hubs)
    hubRoutes = solveHub(instance) 
    hubRoutes = parseToDayHubroutes(hubRoutes)
    print(hubRoutes)
    hubRoutes = localSearchHubRoutes(instance, hubRoutes, maxTimeSeconds=5, nStart=20)
    print(hubRoutes)
    hubRoutesDict = hubRoutes.toDict(instance)
   
    depotRoutes = {}
    dmin = min([_.daysFresh for _ in instance.Products])
     
    for i in range(0, math.ceil(nDays/dmin)):  
        periodBegin = dmin*i+1
        periodEnd = dmin*(i+1)+1
        print(i, periodBegin, periodEnd)
        period = list(range(periodBegin, periodEnd))
        periodRoutes = extractDays(hubRoutesDict, period)
        if len(periodRoutes)>0:                                                #depot routing
            res = solveDepotVRP(instance, periodRoutes)
            depotRoutes[periodBegin] = res
        else:
            depotRoutes[periodBegin] = {}

    return {'hubRoutes': hubRoutesDict, 'depotRoutes': depotRoutes}

In [11]:
def solutionToStr(instance: InstanceCO22, res: dict):
    resultString = "DATASET = CO2022_11 \n \n"

    for day in range(1, instance.Days+1):
        resultString += f"DAY = {day} \n"

        truckString = ""
        if day in res['depotRoutes'].keys():
            nTrucks = len(res['depotRoutes'][day])
            for routeID, truckRoute in res['depotRoutes'][day].items():
                truckString += f"{routeID} "
                for i, hubData in enumerate(truckRoute[1:-1]):
                    amountPerProduct = hubData['amounts']
                    truckString += f"H{hubData['locID'] - 1} {','.join([str(_) for _ in amountPerProduct])} "
                truckString += "\n"
        else:
            nTrucks = 0
            
        resultString += f"NUMBER_OF_TRUCKS = {nTrucks} \n"
        resultString += truckString

        nVans = 0
        i = 0
        vanString = ""
        for hubLocID in res['hubRoutes'][day].keys():
            for _, route in res['hubRoutes'][day][hubLocID]['routes'].items():
                i+=1
                reqIds = [_['reqID'] for _ in route['route'][1:-1] ]
                vanString += f"{i} H{hubLocID-1} {' '.join([str(_) for _ in reqIds])} \n"
            nVans += len(res['hubRoutes'][day][hubLocID]['routes'])
        resultString += f"NUMBER_OF_VANS = {nVans} \n"  
        resultString += vanString + "\n"
    return resultString
    

In [13]:
i = 4
instance = loadInstance(i)
res = solve(instance)
solutionStr = solutionToStr(instance,res)
with open(f"./greedy01ls/solution{i}.txt" ,'w') as file:
    file.write(solutionStr)

INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 256 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 256.0
INFO:vrpy.vrp:iteration 1, 256.0
INFO:vrpy.vrp:iteration 2, 256.0
INFO:vrpy.master_solve_pulp:total cost = 256.0
INFO:vrpy.vrp:new upper bound : max num stops = 3


[25, 29] []
[3, 8, 17, 24, 38, 39] []
[6, 11, 15, 20, 36, 41, 43, 46] []
[1, 2, 9, 12, 13, 16, 18, 19, 21, 22, 23, 27, 28, 30, 32, 33, 34, 35, 37, 40, 42, 44, 45, 47, 48, 49, 50] [1, 2]
[4, 5, 7, 10, 14, 26, 31] []
[25, 29] []
[3, 8, 17, 24, 38, 39] [3]


INFO:vrpy.vrp:Clarke & Wright solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 150.0
INFO:vrpy.master_solve_pulp:total cost = 150.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 254 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 254 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 254.0
INFO:vrpy.vrp:iteration 1, 254.0
INFO:vrpy.vrp:iteration 2, 254.0
INFO:vrpy.master_solve_pulp:total cost = 254.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 156 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 156 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 156.0


[6, 11, 15, 20, 36, 41, 43, 46] []
[1, 2, 9, 12, 13, 16, 18, 19, 21, 22, 23, 27, 28, 30, 32, 33, 34, 35, 37, 40, 42, 44, 45, 47, 48, 49, 50] []
[4, 5, 7, 10, 14, 26, 31] []
[25, 29] []
[3, 8, 17, 24, 38, 39] []
[6, 11, 15, 20, 36, 41, 43, 46] []
[1, 2, 9, 12, 13, 16, 18, 19, 21, 22, 23, 27, 28, 30, 32, 33, 34, 35, 37, 40, 42, 44, 45, 47, 48, 49, 50] []
[4, 5, 7, 10, 14, 26, 31] [4, 5]
[25, 29] []
[3, 8, 17, 24, 38, 39] [8]


INFO:vrpy.master_solve_pulp:total cost = 156.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 218 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 218 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 218.0
INFO:vrpy.master_solve_pulp:total cost = 218.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 150 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 150.0
INFO:vrpy.master_solve_pulp:total cost = 150.0
INFO:vrpy.vrp:new upper bound : max num stops = 3
INFO:vrpy.vrp:Clarke & Wright solution found with value 252 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 252 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 252.0


...

{1: ['Source', '5.1', '6.1', '3.1', '4.1', 'Sink']}
{1: [{'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 5, 'demand': 16, 'amounts': [8, 0, 8], 'X': 74, 'Y': 63, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 6, 'demand': 34, 'amounts': [8, 12, 14], 'X': 71, 'Y': 87, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 3, 'demand': 11, 'amounts': [0, 5, 6], 'X': 33, 'Y': 82, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 4, 'demand': 14, 'amounts': [6, 8, 0], 'X': 21, 'Y': 68, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 57, 'frequency': 1}]}
1 5 9
dict_keys(['4.1', '6.1', '5.1', 'Source', 'Sink'])
{1: ['Source', '4.1', '6.1', '5.1', 'Sink']}
{1: [{'locID': 1, 'X': 76, 'Y': 57, '

INFO:vrpy.vrp:Clarke & Wright solution found with value 412 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 412 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 412.0
INFO:vrpy.vrp:iteration 1, 412.0
INFO:vrpy.vrp:iteration 2, 412.0
INFO:vrpy.vrp:iteration 3, 412.0
INFO:vrpy.vrp:iteration 4, 412.0
INFO:vrpy.vrp:iteration 5, 412.0
INFO:vrpy.vrp:iteration 6, 412.0
INFO:vrpy.master_solve_pulp:total cost = 412.0
INFO:vrpy.vrp:new upper bound : max num stops = 5
INFO:vrpy.vrp:Clarke & Wright solution found with value 329 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 329 and 1 vehicles
INFO:vrpy.vrp:iteration 0, 329.0
INFO:vrpy.vrp:iteration 1, 329.0
INFO:vrpy.vrp:iteration 2, 329.0
INFO:vrpy.vrp:iteration 3, 329.0
INFO:vrpy.master_solve_pulp:total cost = 329.0
INFO:vrpy.vrp:new upper bound : max num stops = 4
INFO:vrpy.vrp:Clarke & Wright solution found with value 318 and 1 vehicles
INFO:vrpy.vrp:Greedy solution found with value 318 and 1 vehicles
INFO:vrpy.vrp:iterat

{1: ['Source', '5.1', '6.1', '3.1', '2.1', 'Sink']}
{1: [{'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 5, 'demand': 66, 'amounts': [31, 20, 15], 'X': 74, 'Y': 63, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 6, 'demand': 12, 'amounts': [0, 7, 5], 'X': 71, 'Y': 87, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 3, 'demand': 8, 'amounts': [0, 0, 8], 'X': 33, 'Y': 82, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 2, 'demand': 12, 'amounts': [5, 7, 0], 'X': 4, 'Y': 27, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 78, 'frequency': 1}]}
3 13 17
dict_keys(['5.1', '4.1', '3.1', 'Source', 'Sink'])
{1: ['Source', '4.1', '3.1', '5.1', 'Sink']}
{1: [{'locID': 1, 'X': 76, 'Y': 57, 

INFO:vrpy.vrp:iteration 1, 318.0
INFO:vrpy.vrp:iteration 2, 318.0
INFO:vrpy.master_solve_pulp:total cost = 318.0


{1: ['Source', '5.1', '4.1', 'Sink']}
{1: [{'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 5, 'demand': 81, 'amounts': [19, 27, 35], 'X': 74, 'Y': 63, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 4, 'demand': 11, 'amounts': [6, 0, 5], 'X': 21, 'Y': 68, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 0, 'frequency': 1}, {'locID': 1, 'X': 76, 'Y': 57, 'demand': 0, 'collect': 0, 'service_time': 0, 'lower': 0, 'upper': 57, 'frequency': 1}]}


In [824]:
for i in range(20):
    print(i)
    instance = loadInstance(i)
    res = solve(instance)
    solutionStr = solutionToStr(instance,res)
    with open(f"./greedy01ls/solution{i}.txt" ,'w') as file:
        file.write(solutionStr)

0


AttributeError: 'InstanceCO22' object has no attribute 'Days'